Import des modules utiles. 

In [5]:
import csv
import pathlib
import numpy as np
import pandas as pd
import folium
from folium.plugins import MarkerCluster, HeatMap
from scipy.spatial import ConvexHull
from scipy.spatial import Delaunay
from shapely.geometry import Polygon
from shapely.geometry import Point
from shapely.ops import unary_union
from scipy.spatial import distance_matrix
import alphashape

Chargement des données depuis le fichier CSV vers un dataframe Pandas. 

In [6]:
with open('/home/wsl/storage/Documents/BPE23/BPE23.csv', 'r') as csvfile:
    reader = csv.DictReader(csvfile, delimiter=';')
    for i, row in enumerate(reader):
        if i > 10:
            break
        print(row)
    

{'AN': '2023', 'NOMRS': 'COMMISSARIAT DE POLICE DE POINTE À PITRE', 'CNOMRS': '', 'NUMVOIE': '', 'INDREP': '', 'TYPVOIE': '', 'LIBVOIE': 'QUARTIER LAFOND', 'CADR': '', 'LIBCOM': 'LES ABYMES', 'CODPOS': '97139', 'DEPCOM': '97101', 'DEP': '971', 'REG': '01', 'DOM': 'A', 'SDOM': 'A1', 'TYPEQU': 'A101', 'SIRET': '', 'STATUT_DIFFUSION': '_Z', 'CANTINE': '_Z', 'INTERNAT': '_Z', 'RPI': '_Z', 'EP': '_Z', 'CL_PGE': '_Z', 'SECT': '_Z', 'ACCES_AIRE_PRATIQUE': '_Z', 'ACCES_LIBRE': '_Z', 'ACCES_SANITAIRE': '_Z', 'ACCES_VESTIAIRE': '_Z', 'CAPACITE_D_ACCUEIL': '_Z', 'PRES_DOUCHE': '_Z', 'PRES_SANITAIRE': '_Z', 'SAISONNIER': '_Z', 'COUVERT': '_Z', 'ECLAIRE': '_Z', 'CATEGORIE': '_Z', 'MULTIPLEXE': '_Z', 'ACCUEIL': '_Z', 'ITINERANCE': '_Z', 'MODE_GESTION': '_Z', 'SSTYPHEB': '_Z', 'TYPE': '_Z', 'CAPACITE': '', 'INDIC_CAPA': '0', 'NBEQUIDENT': '', 'INDIC_NBEQUIDENT': '0', 'NBSALLES': '', 'INDIC_NBSALLES': '0', 'NBLIEUX': '', 'INDIC_NBLIEUX': '0', 'LAMBERT_X': '657375.042365704', 'LAMBERT_Y': '1795994.2288

In [7]:
df_bpe = pd.read_csv('/home/wsl/storage/Documents/BPE23/BPE23.csv', delimiter=';')
df_bpe = df_bpe.astype({
    'DEPCOM': 'string',
    'DEP': 'string',
    'QUALI_IRIS': 'Int64',
    'QUALI_QP2015': 'Int64',
    'QUALI_QP': 'Int64',
    'QUALI_QVA': 'Int64',
    'QUALI_ZUS': 'Int64',
    'EPCI': 'string',
    'UU2020': 'string',
    'BV2022': 'string',
    'AAV2020': 'string'
}, errors='ignore', copy=True)
# Display the first few rows of the DataFrame
print(df_bpe.head())
# Display the shape of the DataFrame
print(df_bpe.shape)
# Display the column names of the DataFrame
print(df_bpe.columns)
# Display the data types of the columns in the DataFrame
print(df_bpe.dtypes)

/tmp/ipykernel_55613/675851971.py:1: DtypeWarning: Columns (10,11,58,61,63,65,67,68,69,70,71) have mixed types. Specify dtype option on import or set low_memory=False.
  df_bpe = pd.read_csv('/home/wsl/storage/Documents/BPE23/BPE23.csv', delimiter=';')


     AN                                     NOMRS  \
0  2023  COMMISSARIAT DE POLICE DE POINTE À PITRE   
1  2023     DIR REG FINANCES PUBLIQUES GUADELOUPE   
2  2023     DIR REG FINANCES PUBLIQUES GUADELOUPE   
3  2023                      APE ABYMES DOTHEMARE   
4  2023                         APE ABYMES CARUEL   

                                         CNOMRS  NUMVOIE INDREP TYPVOIE  \
0                                           NaN      NaN    NaN     NaN   
1  SCE IMPOTS DES ENTREPRISES GRANDE TERRE NORD      NaN    NaN     RUE   
2                        CFD DE ANTILLES-GUYANE      NaN    NaN     NaN   
3                                           NaN     16.0    NaN     ZAC   
4                                           NaN      NaN    NaN      AV   

              LIBVOIE                     CADR      LIBCOM   CODPOS  ...  QVA  \
0     QUARTIER LAFOND                      NaN  LES ABYMES  97139.0  ...  IND   
1        DES FINANCES  CTRE FINANCES PUBLIQUES  LES ABYMES  97139.0 

In [8]:
df_bpe.describe()

AN       NUMVOIE        CODPOS           REG         SIRET  \
count  2773455.0  2.138252e+06  2.691125e+06  2.773455e+06  2.041944e+06   
mean      2023.0  9.239740e+01  5.406321e+04  5.149248e+01  6.662732e+13   
std          0.0  3.416389e+02  2.801902e+04  3.006515e+01  2.234798e+13   
min       2023.0  0.000000e+00  1.000000e+03  1.000000e+00  5.541552e+11   
25%       2023.0  7.000000e+00  3.126000e+04  2.700000e+01  4.535162e+13   
50%       2023.0  2.000000e+01  5.910000e+04  5.200000e+01  7.947250e+13   
75%       2023.0  5.800000e+01  7.680000e+04  7.600000e+01  8.525024e+13   
max       2023.0  2.272400e+04  9.789900e+04  9.400000e+01  9.999903e+13   

           CAPACITE    INDIC_CAPA     NBEQUIDENT  INDIC_NBEQUIDENT  \
count  1.326540e+05  2.773455e+06  216253.000000      2.773455e+06   
mean   1.414922e+03  4.904136e-02       1.468340      7.797242e-02   
std    1.876095e+05  2.159544e-01       1.328459      2.681282e-01   
min    0.000000e+00  0.000000e+00       1.000000      0.000000e+00   
25%    3.000000e+01  0.000000e+00       1.000000      0.000000e+00   
50%    7.000000e+01  0.000000e+00       1.000000      0.000000e+00   
75%    1.510000e+02  0.000000e+00       1.000000      0.000000e+00   
max    5.746217e+07  1.000000e+00     157.000000      1.000000e+00   

          NBSALLES  ...      NBLIEUX  INDIC_NBLIEUX     LAMBERT_X  \
count  1037.000000  ...  1827.000000   2.773455e+06  2.681236e+06   
mean      1.236258  ...     1.625068   6.587451e-04  6.800848e+05   
std       0.528271  ...     1.481202   2.565758e-02  2.111960e+05   
min       1.000000  ...     1.000000   0.000000e+00  9.997146e+04   
25%       1.000000  ...     1.000000   0.000000e+00  5.585793e+05   
50%       1.000000  ...     1.000000   0.000000e+00  6.610719e+05   
75%       1.000000  ...     2.000000   0.000000e+00  8.455215e+05   
max       5.000000  ...    18.000000   1.000000e+00  1.268898e+06   

          LAMBERT_Y     LONGITUDE      LATITUDE          EPSG        IRISEE  \
count  2.681236e+06  2.681236e+06  2.681236e+06  2.773455e+06  2.773455e+06   
mean   6.561390e+06  2.381635e+00  4.541152e+01  2.216102e+03  6.195363e-01   
std    7.109576e+05  1.023817e+01  8.752938e+00  4.098963e+02  4.855009e-01   
min    2.486076e+05 -6.180817e+01 -2.138701e+01  2.154000e+03  0.000000e+00   
25%    6.380850e+06  1.087990e+00  4.427041e+01  2.154000e+03  0.000000e+00   
50%    6.688952e+06  2.481206e+00  4.713567e+01  2.154000e+03  1.000000e+00   
75%    6.862036e+06  4.928174e+00  4.883993e+01  2.154000e+03  1.000000e+00   
max    7.691250e+06  5.582908e+01  5.108426e+01  5.490000e+03  1.000000e+00   

              DENS3         DENS7  
count  2.773455e+06  2.773455e+06  
mean   1.930935e+00  2.989684e+00  
std    8.297498e-01  1.986930e+00  
min    1.000000e+00  1.000000e+00  
25%    1.000000e+00  1.000000e+00  
50%    2.000000e+00  2.000000e+00  
75%    3.000000e+00  5.000000e+00  
max    3.000000e+00  7.000000e+00  

[8 rows x 21 columns]

In [9]:
df_bpe.dtypes[[10,11,58,61,63,65,67,68,69,70,71]]

/tmp/ipykernel_55613/907554854.py:1: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  df_bpe.dtypes[[10,11,58,61,63,65,67,68,69,70,71]]


DEPCOM          string[python]
DEP             string[python]
QUALI_IRIS              object
QUALI_QP2015            object
QUALI_QP                object
QUALI_QVA               object
QUALI_ZUS               object
EPCI            string[python]
UU2020          string[python]
BV2022          string[python]
AAV2020         string[python]
dtype: object

In [10]:
# df_bpe2 = df_bpe.astype({
#     'DEPCOM': 'string',
#     'DEP': 'string',
#     'QUALI_IRIS': 'Int64',
#     'QUALI_QP2015': 'Int64',
#     'QUALI_QP': 'Int64',
#     'QUALI_QVA': 'Int64',
#     'QUALI_ZUS': 'Int64',
#     'EPCI': 'string',
#     'UU2020': 'string',
#     'BV2022': 'string',
#     'AAV2020': 'string'
# }, errors='raise', copy=True)
# # Display the data types of the columns after conversion
# print(df_bpe2.dtypes[[10, 11, 58, 61, 63, 65, 67, 68, 69, 70, 71]])

In [11]:
bpe44_locations = df_bpe[df_bpe['LIBCOM'] == 'GUÉRANDE'][['NOMRS', 'DOM', 'SDOM', 'DCIRIS', 'LATITUDE', 'LONGITUDE']]
bpe44_locations = bpe44_locations.dropna(subset=['LATITUDE', 'LONGITUDE'])
bpe44_locations.isna().sum()

NOMRS        0
DOM          0
SDOM         0
DCIRIS       0
LATITUDE     0
LONGITUDE    0
dtype: int64

In [12]:
# Display all the the locations on a map with "NOMRS" as the label of each point and with a color corresponding to the "DOM" value.
center_location = bpe44_locations[['LATITUDE', 'LONGITUDE']].mean().tolist()
print(center_location)
DOM_colors = {
    'A': 'blue',
    'B': 'green',
    'C': 'red',
    'D': 'purple',
    'E': 'orange',
    'F': 'darkred',
    'G': 'lightred'
}
m = folium.Map(location=center_location, zoom_start=13)
for _, row in bpe44_locations.iterrows():
    folium.Marker(
        location=[row['LATITUDE'], row['LONGITUDE']],
        popup=row['NOMRS'],
        icon=folium.Icon(color=DOM_colors.get(row['DOM'], 'gray'), icon='info-sign')
    ).add_to(m)
m.save('/home/wsl/storage/Documents/BPE23/bpe44_locations_map.html')

[47.327676019473465, -2.41573262782826]


In [13]:
# Display all the the locations on a map with "NOMRS" as the label of each point and with a color corresponding to the "DOM" value.
center_location = bpe44_locations[['LATITUDE', 'LONGITUDE']].mean().tolist()
print(center_location)
SDOM_colors = {
    # Groupe A - Services (nuances de bleu)
    "A1": "#1E3A8A",    # Services publics - Bleu foncé
    "A2": "#1E40AF",    # Services généraux - Bleu royal
    "A3": "#2563EB",    # Services automobiles - Bleu vif
    "A4": "#3B82F6",    # Artisanat du bâtiment - Bleu clair
    "A5": "#60A5FA",    # Autres services - Bleu pastel
    
    # Groupe B - Commerce (nuances de vert)
    "B1": "#14532D",    # Grandes surfaces - Vert foncé
    "B2": "#166534",    # Commerces alimentaires - Vert sapin
    "B3": "#15803D",    # Commerces spécialisés non-alimentaires - Vert moyen
    
    # Groupe C - Enseignement (nuances d'orange/rouge)
    "C1": "#B91C1C",    # Enseignement du premier degré - Rouge foncé
    "C2": "#DC2626",    # Enseignement du second degré - premier cycle - Rouge vif
    "C3": "#EF4444",    # Enseignement du second degré - second cycle - Rouge clair
    "C4": "#F97316",    # Enseignement supérieur non-universitaire - Orange foncé
    "C5": "#FB923C",    # Enseignement supérieur universitaire - Orange moyen
    "C6": "#FDBA74",    # Formation continue - Orange clair
    "C7": "#FED7AA",    # Autres services de l'éducation - Orange pastel
    
    # Groupe D - Santé et action sociale (nuances de violet/magenta)
    "D1": "#581C87",    # Etablissements et services de santé - Violet foncé
    "D2": "#7C3AED",    # Fonctions médicales et paramédicales - Violet vif
    "D3": "#8B5CF6",    # Autres établissements et services sanitaires - Violet clair
    "D4": "#A855F7",    # Action sociale pour personnes âgées - Magenta foncé
    "D5": "#C084FC",    # Action sociale pour enfants en bas-âge - Magenta moyen
    "D6": "#DDD6FE",    # Action sociale pour handicapés - Magenta clair
    "D7": "#EDE9FE",    # Autres services d'action sociale - Magenta pastel
    
    # Groupe E - Infrastructures (nuance de gris)
    "E1": "#374151",    # Infrastructures de transports - Gris foncé
    
    # Groupe F - Équipements (nuances de cyan/turquoise)
    "F1": "#0E7490",    # Equipements sportifs - Cyan foncé
    "F2": "#0891B2",    # Equipements de loisirs - Cyan moyen
    "F3": "#06B6D4",    # Equipements culturels et socioculturels - Cyan clair
    
    # Groupe G - Tourisme (nuance de jaune)
    "G1": "#D97706"     # Tourisme - Jaune/ambre
}
SDOM_descriptions = {
    "A1": "Services publics",
    "A2": "Services généraux", 
    "A3": "Services automobiles",
    "A4": "Artisanat du bâtiment",
    "A5": "Autres services",
    "B1": "Grandes surfaces",
    "B2": "Commerces alimentaires",
    "B3": "Commerces spécialisés non-alimentaires",
    "C1": "Enseignement du premier degré",
    "C2": "Enseignement du second degré - premier cycle",
    "C3": "Enseignement du second degré - second cycle", 
    "C4": "Enseignement supérieur non-universitaire",
    "C5": "Enseignement supérieur universitaire",
    "C6": "Formation continue",
    "C7": "Autres services de l'éducation",
    "D1": "Etablissements et services de santé",
    "D2": "Fonctions médicales et paramédicales (à titre libéral)",
    "D3": "Autres établissements et services à caractère sanitaire",
    "D4": "Action sociale pour personnes âgées",
    "D5": "Action sociale pour enfants en bas-âge",
    "D6": "Action sociale pour handicapés",
    "D7": "Autres services d'action sociale",
    "E1": "Infrastructures de transports",
    "F1": "Equipements sportifs",
    "F2": "Equipements de loisirs", 
    "F3": "Equipements culturels et socioculturels",
    "G1": "Tourisme"
}

# Dictionnaire des couleurs par code
categories_colors = {
    "A1": "#1E3A8A", "A2": "#1E40AF", "A3": "#2563EB", "A4": "#3B82F6", "A5": "#60A5FA",
    "B1": "#14532D", "B2": "#166534", "B3": "#15803D",
    "C1": "#B91C1C", "C2": "#DC2626", "C3": "#EF4444", "C4": "#F97316", "C5": "#FB923C", "C6": "#FDBA74", "C7": "#FED7AA",
    "D1": "#581C87", "D2": "#7C3AED", "D3": "#8B5CF6", "D4": "#A855F7", "D5": "#C084FC", "D6": "#DDD6FE", "D7": "#EDE9FE",
    "E1": "#374151", "F1": "#0E7490", "F2": "#0891B2", "F3": "#06B6D4", "G1": "#D97706"
}

# Descriptions détaillées par code
categories_labels = {
    "A1": "Services publics", "A2": "Services généraux", "A3": "Services automobiles", "A4": "Artisanat du bâtiment", "A5": "Autres services",
    "B1": "Grandes surfaces", "B2": "Commerces alimentaires", "B3": "Commerces spécialisés",
    "C1": "Enseignement primaire", "C2": "Collège", "C3": "Lycée", "C4": "Enseignement sup. non-univ", "C5": "Université", "C6": "Formation continue", "C7": "Autres éducation",
    "D1": "Établissements santé", "D2": "Médecins libéraux", "D3": "Autres services sanitaires", "D4": "Aide personnes âgées", "D5": "Aide petite enfance", "D6": "Aide handicapés", "D7": "Autres services sociaux",
    "E1": "Infrastructures transports",
    "F1": "Équipements sportifs", "F2": "Équipements loisirs", "F3": "Équipements culturels",
    "G1": "Tourisme"
}

# Groupes organisés
legend_groups = [
    ("Services", ["A1", "A2", "A3", "A4", "A5"]),
    ("Commerce", ["B1", "B2", "B3"]),
    ("Enseignement", ["C1", "C2", "C3", "C4", "C5", "C6", "C7"]),
    ("Santé & Social", ["D1", "D2", "D3", "D4", "D5", "D6", "D7"]),
    ("Infrastructures", ["E1"]),
    ("Équipements", ["F1", "F2", "F3"]),
    ("Tourisme", ["G1"])
]

def add_detailed_legend(folium_map):
    """Ajoute une légende détaillée avec tous les codes à la carte Folium"""
    
    items = ""
    for group_name, codes in legend_groups:
        items += f'<div style="margin:6px 0;"><b>{group_name}:</b></div>'
        for code in codes:
            color = categories_colors[code]
            label = categories_labels[code]
            items += f'''<div style="margin:1px 0 1px 8px;font-size:10px;">
                <span style="display:inline-block;width:10px;height:10px;background:{color};margin-right:4px;"></span>
                <b>{code}</b> {label}
            </div>'''
    
    legend_html = f'''
    <div style="position:fixed;top:10px;right:10px;width:220px;max-height:400px;
                background:white;border:2px solid grey;z-index:9999;font-size:11px;
                padding:8px;border-radius:5px;box-shadow:0 2px 5px rgba(0,0,0,0.2);
                overflow-y:auto;">
        <h4 style="margin:0 0 8px 0;font-size:13px;">Détail des catégories</h4>
        {items}
    </div>'''
    
    folium_map.get_root().html.add_child(folium.Element(legend_html))
    return folium_map

def add_compact_legend(folium_map):
    """Ajoute une légende compacte groupée à la carte Folium"""
    
    group_colors = {"Services": "#2563EB", "Commerce": "#166534", "Enseignement": "#F97316", 
                   "Santé & Social": "#7C3AED", "Infrastructures": "#374151", "Équipements": "#0891B2", "Tourisme": "#D97706"}
    
    items = "".join([f'''<div style="margin:3px 0;">
        <span style="display:inline-block;width:12px;height:12px;background:{group_colors[name]};margin-right:5px;"></span>
        <b>{name}</b> <span style="font-size:10px;color:#666;">({len(codes)} types)</span>
    </div>''' for name, codes in legend_groups])
    
    legend_html = f'''
    <div style="position:fixed;top:10px;left:50px;width:180px;background:white;
                border:2px solid grey;z-index:9999;font-size:12px;padding:8px;
                border-radius:5px;box-shadow:0 2px 5px rgba(0,0,0,0.2);">
        <h4 style="margin:0 0 8px 0;">Catégories</h4>{items}
    </div>'''
    
    folium_map.get_root().html.add_child(folium.Element(legend_html))
    return folium_map

# Create a Folium map centered on the average location of the points
m = folium.Map(location=center_location, zoom_start=13)

# Add a legend to the map to indicate the meaning of each color
# add_detailed_legend(m)
add_compact_legend(m)

# Add circle markers for each location with color based on "SDOM"
for _, row in bpe44_locations.iterrows():
    folium.CircleMarker(
        location=[row['LATITUDE'], row['LONGITUDE']],
        radius=1,
        popup=row['NOMRS'],
        color=SDOM_colors.get(row['SDOM'], 'gray'),
        fill=True,
        fill_color=SDOM_colors.get(row['SDOM'], 'gray'),
        fill_opacity=0.6
    ).add_to(m)


# # Add a concave hull (alpha shape) for each unique "DCIRIS" value
# unique_dciris = bpe44_locations['DCIRIS'].unique()
# def alpha_shape(points, alpha):
#     """Compute the alpha shape (concave hull) of a set of points."""
#     if len(points) < 4:
#         return None  # Not enough points to form a shape
#     tri = Delaunay(points)
#     edges = set()
#     for simplex in tri.simplices:
#         for i in range(len(simplex)):
#             edge = (simplex[i], simplex[(i + 1) % len(simplex)])
#             edges.add(edge)
#     edges = np.array(list(edges))
    
#     # Calculate edge lengths
#     lengths = np.linalg.norm(points[edges[:, 0]] - points[edges[:, 1]], axis=1)
    
#     # Filter edges based on alpha
#     filtered_edges = edges[lengths < alpha]
    
#     if len(filtered_edges) == 0:
#         return None
    
#     # Create a polygon from the filtered edges
#     polygon = Polygon(points[filtered_edges].reshape(-1, 2))
    
#     return polygon
# # Loop through each unique "DCIRIS" value and create a concave hull
# for dciris in unique_dciris:
#     subset = bpe44_locations[bpe44_locations['DCIRIS'] == dciris]
#     if not subset.empty:
#         points = subset[['LATITUDE', 'LONGITUDE']].values
#         if len(points) > 3:  # Alpha shape requires at least 4 points
#             alpha = 0.1  # Adjust alpha as needed
#             hull_polygon = alpha_shape(points, alpha)
#             if hull_polygon is not None:
#                 hull_polygon = folium.Polygon(
#                     locations=hull_polygon.exterior.coords,
#                     color='black',
#                     fill=True,
#                     fill_color='black',
#                     fill_opacity=0.1,
#                     weight=1
#                 )
#                 m.add_child(hull_polygon)


# # Couleurs pour les 8 valeurs DCIRIS
# dciris_colors = {
#     1: "#FF5733", 2: "#33FF57", 3: "#3357FF", 4: "#FF33F1",
#     5: "#33FFF1", 6: "#F1FF33", 7: "#FF8C33", 8: "#8C33FF"
# }

# def create_alpha_shape(points, alpha=0.5):
#     """Crée une alpha shape à partir d'une liste de points"""
#     if len(points) < 3:
#         return None
#     try:
#         # Convertir en array numpy
#         coords = np.array([[p[0], p[1]] for p in points])
#         # Créer l'alpha shape
#         alpha_shape = alphashape.alphashape(coords, alpha)
#         return alpha_shape
#     except:
#         return None

# def points_to_folium_coords(geometry):
#     """Convertit une géométrie Shapely en coordonnées Folium"""
#     if geometry is None or geometry.is_empty:
#         return []
    
#     if geometry.geom_type == 'Polygon':
#         return [[coord[1], coord[0]] for coord in geometry.exterior.coords]
#     elif geometry.geom_type == 'MultiPolygon':
#         return [[[coord[1], coord[0]] for coord in poly.exterior.coords] for poly in geometry.geoms]
#     return []

# def add_concave_hulls(folium_map, data, alpha=0.5):
#     """
#     Ajoute les concave hulls à la carte Folium
    
#     Args:
#         folium_map: Carte Folium
#         data: Liste de dict avec 'lat', 'lon', 'DCIRIS'
#         alpha: Paramètre alpha pour les shapes (plus petit = plus concave)
#     """
    
#     # Grouper les points par DCIRIS
#     dciris_groups = {}
#     for _, point in data.iterrows():
#         dciris = point['DCIRIS']
#         if dciris not in dciris_groups:
#             dciris_groups[dciris] = []
#         dciris_groups[dciris].append([point['LATITUDE'], point['LONGITUDE']])
    
#     # Créer les hulls pour chaque groupe
#     for dciris, points in dciris_groups.items():
#         print(f"Processing DCIRIS {dciris} with {len(points)} points")
#         if len(points) < 3:
#             continue
            
#         # Créer l'alpha shape
#         alpha_shape = create_alpha_shape(points, alpha)
#         if alpha_shape is None:
#             print(f"Alpha shape creation failed for DCIRIS {dciris} with {len(points)} points")
#             continue
        
#         # Convertir en coordonnées Folium
#         coords = points_to_folium_coords(alpha_shape)
#         if not coords:
#             print(f"No valid coordinates for DCIRIS {dciris}")
#             continue
        
#         color = dciris_colors.get(dciris, "#808080")
        
#         # Ajouter à la carte
#         if isinstance(coords[0][0], list):  # MultiPolygon
#             print(f"Adding MultiPolygon for DCIRIS {dciris}")
#             for poly_coords in coords:
#                 folium.Polygon(
#                     locations=poly_coords,
#                     color=color,
#                     weight=2,
#                     fillColor=color,
#                     fillOpacity=0.2,
#                     popup=f"DCIRIS: {dciris}"
#                 ).add_to(folium_map)
#         else:  # Polygon simple
#             print(f"Adding Polygon for DCIRIS {dciris}")
#             folium.Polygon(
#                 locations=coords,
#                 color=color,
#                 weight=2,
#                 fillColor=color,
#                 fillOpacity=0.2,
#                 popup=f"DCIRIS: {dciris}"
#             ).add_to(folium_map)
    
#     return folium_map

# def add_hulls_simple(folium_map, data, buffer_size=0.001):
#     """
#     Version simplifiée utilisant des buffers au lieu d'alpha shapes
#     Plus rapide mais moins précis
#     """
    
#     # Grouper par DCIRIS
#     dciris_groups = {}
#     for _, point in data.iterrows():
#         dciris = point['DCIRIS']
#         if dciris not in dciris_groups:
#             dciris_groups[dciris] = []
#         dciris_groups[dciris].append(Point(point['LONGITUDE'], point['LATITUDE']))
    
#     # Créer les hulls avec buffer
#     for dciris, points in dciris_groups.items():
#         if len(points) < 2:
#             print(f"Not enough points for DCIRIS {dciris}: {len(points)} points")
#             continue
        
#         try:
#             # Créer un buffer autour de chaque point et les unir
#             buffered_points = [p.buffer(buffer_size) for p in points]
#             hull = unary_union(buffered_points).convex_hull
            
#             # Convertir en coordonnées Folium
#             coords = [[coord[1], coord[0]] for coord in hull.exterior.coords]
#             color = dciris_colors.get(dciris, "#808080")
            
#             folium.Polygon(
#                 locations=coords,
#                 color=color,
#                 weight=2,
#                 fillColor=color,
#                 fillOpacity=0.2,
#                 popup=f"DCIRIS: {dciris}"
#             ).add_to(folium_map)
#         except:
#             continue
    
#     return folium_map

# # add_hulls_simple(m, bpe44_locations, buffer_size=0.001)
# add_concave_hulls(m, bpe44_locations, alpha=0.5)


# Fonction pour créer concave hull d'une zone
def create_concave_hull(points, alpha=3.5):
    """Crée un concave hull à partir de points lat/lon"""
    coords = [(lon, lat) for lat, lon in points]
    hull = alphashape.alphashape(coords, alpha)
    if hull.is_empty:
        return None
    # Convertir en coordonnées folium (lat, lon)
    if hasattr(hull, 'exterior'):
        return [(lat, lon) for lon, lat in hull.exterior.coords]
    return None

# Ajouter les concave hulls par zone DCIRIS
colors = ['red', 'blue', 'green', 'purple', 'orange', 'darkred', 'lightred', 'beige']

for i, zone in enumerate(bpe44_locations['DCIRIS'].unique()):
    zone_data = bpe44_locations[bpe44_locations['DCIRIS'] == zone]
    points = list(zip(zone_data['LATITUDE'], zone_data['LONGITUDE']))
    
    hull_coords = create_concave_hull(points, alpha=100.0)
    if hull_coords:
        folium.Polygon(
            locations=hull_coords,
            color=colors[i % len(colors)],
            weight=2,
            fillOpacity=0.1,
            popup=f'Zone {zone}'
        ).add_to(m)


# # Add a convex hull for each unique "DCIRIS" value
# unique_dciris = bpe44_locations['DCIRIS'].unique()
# for dciris in unique_dciris:
#     subset = bpe44_locations[bpe44_locations['DCIRIS'] == dciris]
#     if not subset.empty:
#         points = subset[['LATITUDE', 'LONGITUDE']].values
#         if len(points) > 2:  # Convex hull requires at least 3 points
#             hull = ConvexHull(points)
#             hull_points = points[hull.vertices]
#             hull_polygon = folium.Polygon(
#                 locations=hull_points.tolist(),
#                 color='black',
#                 fill=True,
#                 fill_color='black',
#                 fill_opacity=0.1,
#                 weight=1
#             )
#             m.add_child(hull_polygon)


# Save the map to an HTML file
m.save('/home/wsl/storage/Documents/BPE23/bpe44_locations_map.html')

[47.327676019473465, -2.41573262782826]


In [14]:
# Display the map in a Jupyter Notebook
# m

In [15]:
class BPEMapVisualizer:
    """Visualisateur optimisé pour les données BPE avec Folium"""
    
    def __init__(self):
        # Configuration des couleurs par domaine (version concise)
        self.colors = {
            "A1": "#1E3A8A", "A2": "#1E40AF", "A3": "#2563EB", "A4": "#3B82F6", "A5": "#60A5FA",
            "B1": "#14532D", "B2": "#166534", "B3": "#15803D",
            "C1": "#B91C1C", "C2": "#DC2626", "C3": "#EF4444", "C4": "#F97316", 
            "C5": "#FB923C", "C6": "#FDBA74", "C7": "#FED7AA",
            "D1": "#581C87", "D2": "#7C3AED", "D3": "#8B5CF6", "D4": "#A855F7",
            "D5": "#C084FC", "D6": "#DDD6FE", "D7": "#EDE9FE",
            "E1": "#374151", "F1": "#0E7490", "F2": "#0891B2", "F3": "#06B6D4", "G1": "#D97706"
        }
        
        # Labels concis
        self.labels = {
            "A1": "Services publics", "A2": "Services généraux", "A3": "Services auto",
            "A4": "Artisanat bâtiment", "A5": "Autres services",
            "B1": "Grandes surfaces", "B2": "Alimentaire", "B3": "Spécialisés",
            "C1": "Primaire", "C2": "Collège", "C3": "Lycée", "C4": "Sup. non-univ",
            "C5": "Université", "C6": "Formation", "C7": "Autres éduc.",
            "D1": "Santé", "D2": "Médecins", "D3": "Sanitaire", "D4": "Personnes âgées",
            "D5": "Petite enfance", "D6": "Handicapés", "D7": "Social",
            "E1": "Transports", "F1": "Sport", "F2": "Loisirs", "F3": "Culture", "G1": "Tourisme"
        }
        
        # Groupes pour légende
        self.groups = [
            ("Services", ["A1", "A2", "A3", "A4", "A5"], "#2563EB"),
            ("Commerce", ["B1", "B2", "B3"], "#166534"),
            ("Enseignement", ["C1", "C2", "C3", "C4", "C5", "C6", "C7"], "#F97316"),
            ("Santé & Social", ["D1", "D2", "D3", "D4", "D5", "D6", "D7"], "#7C3AED"),
            ("Infrastructures", ["E1"], "#374151"),
            ("Équipements", ["F1", "F2", "F3"], "#0891B2"),
            ("Tourisme", ["G1"], "#D97706")
        ]
    
    def create_map(self, data, visualization_type='markers'):
        """
        Crée une carte avec les données BPE
        
        Args:
            data: DataFrame avec colonnes LATITUDE, LONGITUDE, NOMRS, SDOM
            visualization_type: 'markers', 'cluster', 'heatmap'
        """
        # Validation des données
        required_cols = ['LATITUDE', 'LONGITUDE', 'NOMRS', 'SDOM']
        if not all(col in data.columns for col in required_cols):
            raise ValueError(f"Colonnes requises: {required_cols}")
        
        # Centre de la carte
        center = [data['LATITUDE'].mean(), data['LONGITUDE'].mean()]
        
        # Création de la carte optimisée
        m = folium.Map(
            location=center,
            zoom_start=self._calculate_optimal_zoom(data),
            tiles='OpenStreetMap',
            prefer_canvas=True  # Améliore les performances
        )
        
        # Ajout des données selon le type de visualisation
        if visualization_type == 'markers':
            self._add_circle_markers(m, data)
        elif visualization_type == 'cluster':
            self._add_clustered_markers(m, data)
        elif visualization_type == 'heatmap':
            self._add_heatmap(m, data)
        else:
            raise ValueError("Type de visualisation non supporté")
        
        # Ajout de la légende
        self._add_legend(m)
        
        # Ajout des contrôles
        folium.LayerControl().add_to(m)
        
        return m
    
    def _calculate_optimal_zoom(self, data):
        """Calcule le zoom optimal basé sur la dispersion des données"""
        lat_range = data['LATITUDE'].max() - data['LATITUDE'].min()
        lon_range = data['LONGITUDE'].max() - data['LONGITUDE'].min()
        max_range = max(lat_range, lon_range)
        
        if max_range > 1:
            return 9
        elif max_range > 0.5:
            return 10
        elif max_range > 0.1:
            return 12
        else:
            return 13
    
    def _add_circle_markers(self, map_obj, data):
        """Ajoute des marqueurs circulaires optimisés"""
        for _, row in data.iterrows():
            color = self.colors.get(row['SDOM'], '#808080')
            label = self.labels.get(row['SDOM'], 'Inconnu')
            
            # Popup optimisé
            popup_html = f"""
            <div style="font-family:Arial;width:150px;">
                <b>{row['NOMRS']}</b><br>
                <span style="color:{color};">● {row['SDOM']} - {label}</span>
            </div>
            """
            
            folium.CircleMarker(
                location=[row['LATITUDE'], row['LONGITUDE']],
                radius=3,  # Taille réduite pour de meilleures performances
                popup=folium.Popup(popup_html, max_width=200),
                tooltip=f"{row['NOMRS']} ({row['SDOM']})",
                color=color,
                fill=True,
                fillColor=color,
                fillOpacity=0.7,
                weight=1
            ).add_to(map_obj)
    
    def _add_clustered_markers(self, map_obj, data):
        """Ajoute des marqueurs avec clustering pour de gros volumes"""
        # Création des clusters par groupe
        clusters = {}
        for group_name, codes, color in self.groups:
            clusters[group_name] = MarkerCluster(name=group_name).add_to(map_obj)
        
        for _, row in data.iterrows():
            # Trouver le groupe correspondant
            group_name = next(
                (name for name, codes, _ in self.groups if row['SDOM'] in codes),
                "Autres"
            )
            
            if group_name in clusters:
                color = self.colors.get(row['SDOM'], '#808080')
                label = self.labels.get(row['SDOM'], 'Inconnu')
                
                folium.Marker(
                    location=[row['LATITUDE'], row['LONGITUDE']],
                    popup=f"<b>{row['NOMRS']}</b><br>{row['SDOM']} - {label}",
                    tooltip=row['NOMRS'],
                    icon=folium.Icon(color='lightgray', icon='info-sign')
                ).add_to(clusters[group_name])
    
    def _add_heatmap(self, map_obj, data):
        """Ajoute une heatmap des équipements"""
        # Préparation des données pour la heatmap
        heat_data = [[row['LATITUDE'], row['LONGITUDE']] for _, row in data.iterrows()]
        
        HeatMap(
            heat_data,
            min_opacity=0.3,
            radius=15,
            blur=10,
            max_zoom=18
        ).add_to(map_obj)
    
    def _add_legend(self, map_obj):
        """Ajoute une légende compacte"""
        legend_items = ''.join([
            f'''<div style="margin:2px 0;font-size:11px;">
                <span style="display:inline-block;width:10px;height:10px;
                           background:{color};margin-right:5px;"></span>
                <b>{name}</b> ({len(codes)})
            </div>'''
            for name, codes, color in self.groups
        ])
        
        legend_html = f'''
        <div style="position:fixed;top:10px;right:10px;width:150px;
                    background:rgba(255,255,255,0.9);border:1px solid #ccc;
                    z-index:9999;padding:8px;border-radius:5px;
                    box-shadow:0 2px 5px rgba(0,0,0,0.3);">
            <h4 style="margin:0 0 5px 0;font-size:12px;">Équipements</h4>
            {legend_items}
        </div>'''
        
        map_obj.get_root().html.add_child(folium.Element(legend_html))

# ==============================================================================
# UTILISATION SIMPLIFIÉE
# ==============================================================================

def create_bpe_map(data, viz_type='markers'):
    """
    Fonction utilitaire pour créer rapidement une carte BPE
    
    Args:
        data: DataFrame BPE avec LATITUDE, LONGITUDE, NOMRS, SDOM
        viz_type: 'markers', 'cluster', ou 'heatmap'
    
    Returns:
        Carte Folium prête à afficher
    """
    visualizer = BPEMapVisualizer()
    return visualizer.create_map(data, viz_type)

# ==============================================================================
# EXEMPLE D'UTILISATION
# ==============================================================================

# Remplacez 'bpe44_locations' par votre DataFrame
# m = create_bpe_map(bpe44_locations, 'markers')
# m.save('carte_bpe.html')

# Pour un clustering (recommandé si > 1000 points):
# m_cluster = create_bpe_map(bpe44_locations, 'cluster')

# Pour une heatmap:
# m_heat = create_bpe_map(bpe44_locations, 'heatmap')

# ==============================================================================
# FONCTIONS D'ANALYSE AVANCÉES
# ==============================================================================

def analyze_equipment_distribution(data):
    """Analyse rapide de la distribution des équipements"""
    stats = data['SDOM'].value_counts()
    print("Distribution des équipements:")
    for code, count in stats.head(10).items():
        visualizer = BPEMapVisualizer()
        label = visualizer.labels.get(code, code)
        print(f"  {code}: {count:,} ({label})")
    
    return stats

def create_filtered_map(data, sdom_codes, title="Carte filtrée"):
    """Crée une carte avec seulement certains types d'équipements"""
    filtered_data = data[data['SDOM'].isin(sdom_codes)]
    
    if filtered_data.empty:
        print(f"Aucune donnée trouvée pour les codes: {sdom_codes}")
        return None
    
    m = create_bpe_map(filtered_data, 'markers')
    
    # Ajout du titre
    title_html = f'''
    <div style="position:fixed;top:10px;left:50%;transform:translateX(-50%);
                background:rgba(255,255,255,0.9);padding:10px;
                border-radius:5px;z-index:9999;">
        <h3 style="margin:0;text-align:center;">{title}</h3>
        <p style="margin:5px 0 0 0;text-align:center;font-size:12px;">
            {len(filtered_data):,} équipements
        </p>
    </div>'''
    
    m.get_root().html.add_child(folium.Element(title_html))
    return m

# Exemples d'utilisation avancée:

# Analyse de la distribution
# stats = analyze_equipment_distribution(bpe44_locations)

# Carte des équipements de santé uniquement
# health_codes = ['D1', 'D2', 'D3', 'D4', 'D5', 'D6', 'D7']
# health_map = create_filtered_map(bpe44_locations, health_codes, "Équipements de Santé")

# Carte des écoles
# education_codes = ['C1', 'C2', 'C3']
# education_map = create_filtered_map(bpe44_locations, education_codes, "Établissements Scolaires")

In [16]:
marker_map = create_bpe_map(bpe44_locations, 'markers')
marker_map

In [17]:
cluster_map = create_bpe_map(bpe44_locations, 'cluster')
cluster_map

In [18]:
health_map = create_filtered_map(bpe44_locations, ['D1', 'D2', 'D3'], "Équipements de Santé")
health_map

In [19]:
culture_and_tourism_map = create_filtered_map(bpe44_locations, ['F1', 'F2', 'F3', 'G1'], "Équipements Culturels et Touristiques")
culture_and_tourism_map

**Ajout de la base des lieux et des équipements culturels**

In [20]:
import pyarrow.parquet as pq

In [21]:
table_lieuxEquipementsCulturels = pq.read_table('/home/wsl/storage/Documents/BPE23/base-des-lieux-et-des-equipements-culturels/dced78ee-0823-4b61-86e6-57717308d4e4.parquet')
df_lieuxEquipementsCulturels = pd.DataFrame(table_lieuxEquipementsCulturels.to_pandas())
df_lieuxEquipementsCulturels.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 86213 entries, 0 to 86212
Data columns (total 55 columns):
 #   Column                                   Non-Null Count  Dtype  
---  ------                                   --------------  -----  
 0   Source                                   86182 non-null  object 
 1   Nom                                      86213 non-null  object 
 2   Adresse                                  55843 non-null  object 
 3   Complement Adresse                       41 non-null     object 
 4   Code Postal                              86196 non-null  object 
 5   libelle_geographique                     86149 non-null  object 
 6   code_insee                               86213 non-null  object 
 7   Code Insee Arrondt                       86119 non-null  object 
 8   Identifiant origine                      81666 non-null  object 
 9   Type équipement ou lieu                  86213 non-null  object 
 10  Label et appellation                     54486

In [ ]:
df_LEC_filtered = df_lieuxEquipementsCulturels.copy()
df_LEC_filtered